# Author: Tobias

In [1]:
import os 
import datetime
import json
from pathlib import Path
from dotenv import load_dotenv, find_dotenv
import tensorflow as tf

basepath = Path(os.getcwd())
# make sure your working directory is the repository root.
if basepath.name != "idp-radio-1":
    os.chdir(basepath.parent.parent.parent)
load_dotenv(find_dotenv())
basepath = Path(os.getcwd())

%load_ext autoreload
%autoreload 2
basepath

PosixPath('/srv/idp-radio-1')

In [2]:
# Specify which GPU(s) to use
os.environ["CUDA_VISIBLE_DEVICES"] = "1"  # Or 2, 3, etc. other than 0

#config = tf.compat.v1.ConfigProto(device_count={'GPU': 1}, allow_soft_placement=True, log_device_placement=True)
config = tf.compat.v1.ConfigProto(allow_soft_placement=True, log_device_placement=True)
config.gpu_options.allow_growth = True
#config.gpu_options.per_process_gpu_memory_fraction = 1.2
tf.compat.v1.Session(config=config)
tf.__version__

Device mapping:
/job:localhost/replica:0/task:0/device:XLA_CPU:0 -> device: XLA_CPU device
/job:localhost/replica:0/task:0/device:XLA_GPU:0 -> device: XLA_GPU device
/job:localhost/replica:0/task:0/device:GPU:0 -> device: 0, name: GeForce RTX 2080 Ti, pci bus id: 0000:04:00.0, compute capability: 7.5



'2.3.0'

In [19]:
import numpy as np
from sklearn.metrics import classification_report
from tensorflow.keras.metrics import Precision, Recall
from tensorflow.keras import models
from tensorflow.keras.optimizers import Adam, SGD
from keras.utils.generic_utils import get_custom_objects

from tensorflow.keras.applications import InceptionV3, Xception, DenseNet121, InceptionResNetV2, ResNet152V2, NASNetLarge
from src.architectures.simple.simple_base import SimpleBaseArchitecture
from src.architectures.simple.load_model import get_experiment_from_logs, benchmark_from_logs, get_preprocessing_for_architecture, get_model_build_function, rebuild_experiment, difference_test_results
from src.architectures.benchmarks.benchmark import Benchmark, Experiment
from src.architectures.benchmarks.benchmark_definitions import generate_benchmarks,simple_architecture_experiment, Chexpert_Benchmark, CHEXPERT_COLUMNS, METRICS, SINGLE_CLASS_METRICS
from src.metrics.metrics import F2Score
from src.metrics.losses import WeightedBinaryCrossentropy, compute_class_weight

In [4]:
columns_12 = ['Enlarged Cardiomediastinum',
                    'Cardiomegaly',
                    'Lung Opacity',
                    'Lung Lesion',
                    'Edema',
                    'Consolidation',
                    'Pneumonia',
                    'Atelectasis',
                    'Pneumothorax',
                    'Pleural Effusion',
                    'Pleural Other',
                    'Fracture']
columns_5 =  ['Cardiomegaly',
                'Edema',
                'Consolidation',
                'Atelectasis',
                'Pleural Effusion']

uzeros = ['Cardiomegaly',
        'Enlarged Cardiomediastinum',
        'Lung Opacity',
        'Lung Lesion',
        'Consolidation',
        'Pneumothorax',
        'Pleural Effusion']
uones = ['Edema',
        'Atelectasis',
        'Fracture',
        'Pleural Other',
        'Pneumonia',]

upsample_factors = {
    "Enlarged Cardiomediastinum": 1,
    "Lung Lesion":1,
    "Pleural Other":2,
    "Fracture":2,
}

transformations_2 = {"unsharp_mask":{"radius":2, "amount":1}}

In [18]:
chexpert_benchmarks, _ = generate_benchmarks(path = Path(os.environ.get("CHEXPERT_DATASET_DIRECTORY")),
                                             name_suffix="",
                                             classes=columns_12,
                                             train_labels = "train.csv",
                                             test_labels = "test.csv",
                                             nan_replacement = -1, #float("NaN"),
                                             u_enc = "uones",
                                             batch_sizes = {"b": 32},
                                             epoch_sizes = {"e": 3},
                                             dim=(256, 256),
                                             optimizer = SGD(learning_rate=2e-1),
                                             lr_factor = 0.5,
                                             augmentation = None,
                                             crop = {"C0": False},
                                             split_seed = 6122156,
                                             split_valid_size = 0.05, 
                                             preprocess_input_fn = tf.keras.applications.densenet.preprocess_input)

Initialzed custom_binary_crossentropy with epsilon 1e-05
Chestxray_BCE_E3_B32_C0_N12 could not be created
Chestxray_WBCE_E3_B32_C0_N12 could not be created
Chestxray_CWBCE_E3_B32_C0_N12 could not be created


In [19]:
key_bce = [key for key in chexpert_benchmarks.keys() if key.startswith("BCE")][0]
key_bce

'BCE_E3_B32_C0_N12'

In [14]:
#bce_benchmark = chexpert_benchmarks[key_bce]
#bce_benchmark.as_dict()
bce_benchmark = Chexpert_Benchmark (path = Path(os.environ.get("CHEXPERT_DATASET_DIRECTORY")),
                     name="Ensemble_Sharp21_U75_C0_N12_SGD",
                     classes=columns_12,
                     train_labels = "train.csv",
                     test_labels = "test.csv",
                     nan_replacement = 0, #float("NaN"),
                     u_enc = [uzeros, uones],
                     epochs=3,
                      metrics=METRICS,
                      single_class_metrics=SINGLE_CLASS_METRICS,
                     batch_size=32,
                     crop = False,
                     dim=(256, 256),
                     use_class_weights = False,
                     upsample_factors = upsample_factors,
                     transformations = transformations_2,
                     split_seed = 6122156,
                     split_valid_size = 0.05, 
                     preprocess_input_fn = tf.keras.applications.densenet.preprocess_input)

In [15]:
bce_chexpert_exp = simple_architecture_experiment(bce_benchmark, DenseNet121, bce_benchmark.label_columns)

In [16]:
model_name = "DenseNet121_Chexpert_BCE_E3_B32_C0_N12_Uones_D256_DS9505_2LR1_LF5_SGD"
model_name = "DenseNet121_Chexpert_BCE_E3_B32_C0_N12_D256_DS9505_2LR1_LF5_SGD"
model_name = "DenseNet121_Chexpert_CWBCE_L1Normed_E3_B32_C0_N12_AugAffine_sharp21_U75_D256_DS9505_5LR1_LF1_SGD_Upsampled"
model_folder_path = basepath / "models" / model_name
weights_path = model_folder_path / "weights.01-53435377146446896679468671172608.00.hdf5"
weights_path = model_folder_path / "weights.03-0.27.hdf5"
weights_path = model_folder_path / "DenseNet121_Chexpert_CWBCE_L1Normed_E3_B32_C0_N12_AugAffine_sharp21_U75_D256_DS9505_5LR1_LF1_SGD_Upsampled_20200824-121846.h5"
weights_path

PosixPath('/srv/idp-radio-1/models/DenseNet121_Chexpert_CWBCE_L1Normed_E3_B32_C0_N12_AugAffine_sharp21_U75_D256_DS9505_5LR1_LF1_SGD_Upsampled/DenseNet121_Chexpert_CWBCE_L1Normed_E3_B32_C0_N12_AugAffine_sharp21_U75_D256_DS9505_5LR1_LF1_SGD_Upsampled_20200824-121846.h5')

In [22]:
untrained_weights = bce_chexpert_exp.model.get_weights()


In [20]:
untrained_weights

[array([[[[0.0783, 0.0142, 0.00277, -0.0502, -0.00273, -0.0291, 0.0456, 0.00117, -9.15e-09, -0.0297, ..., 0.00475, -0.206, 0.0272,
           -0.0488, 0.0363, 0.0259, -0.00901, -0.00735, -0.0154, -0.0267],
          [0.164, -0.00772, -0.00468, -0.00229, 0.00809, -0.0686, 0.00131, 0.0169, -4.44e-09, -0.0276, ..., 0.0133, 0.0191, 0.0312,
           0.0114, 0.0187, 0.0432, -0.018, 0.0157, -0.0131, 0.128],
          [0.0438, -0.00789, -0.00751, -0.0265, 0.00303, 0.025, -0.0285, -0.0123, 1.73e-09, -0.0352, ..., 0.0137, 0.184, 0.012, 0.0438,
           0.0236, 0.0155, -0.00775, -0.0151, -0.0159, -0.0903]],
 
         [[0.149, 0.0208, -0.00822, 0.00662, 0.00856, -0.139, 0.016, 0.00755, -5.95e-09, 0.00108, ..., -0.0418, -0.141, 0.038, -0.0711,
           -0.0524, 0.0315, 0.0114, -0.0326, -0.0116, -0.0374],
          [0.248, 0.00212, -0.00994, 0.0654, -0.000445, -0.197, 0.00395, 0.00409, 7.45e-09, 0.00764, ..., -0.0439, 0.0031, 0.0606,
           0.0307, -0.0687, 0.0553, 0.00689, -0.0369, -0.00

In [17]:
if not weights_path.exists():
    raise Exception(f"Weights file '{weights_path}' does not exist ")
bce_chexpert_exp.model.load_weights(weights_path)
trained_weights = bce_chexpert_exp.model.get_weights()

In [ ]:
mean_weights = {i:trained_weights[i].mean() for i in range(len(trained_weights))}
mean_weights

In [24]:
trained_weights

[array([[[[0.083, 0.0246, 0.00055, -0.0495, -0.00885, -0.0281, 0.0508, 0.0118, -9.15e-09, -0.0265, ..., 0.00575, -0.212, 0.0222, -0.0491,
           0.0383, 0.0249, -0.0131, 0.00232, -0.0153, -0.029],
          [0.169, 0.0023, -0.00756, -0.00177, 0.00359, -0.0678, 0.00643, 0.0282, -4.44e-09, -0.0245, ..., 0.0139, 0.0127, 0.0265, 0.0122,
           0.0203, 0.0421, -0.0229, 0.0256, -0.0124, 0.126],
          [0.0486, 0.00109, -0.0114, -0.0263, 0.00157, 0.0257, -0.0237, -0.000321, 1.73e-09, -0.0324, ..., 0.0136, 0.179, 0.00801,
           0.0464, 0.0244, 0.0143, -0.0139, -0.00509, -0.0141, -0.0927]],
 
         [[0.151, 0.0263, -0.00423, 0.0144, -9.64e-05, -0.138, 0.0152, 0.0194, -5.95e-09, 0.00632, ..., -0.0352, -0.148, 0.0344, -0.082,
           -0.044, 0.0312, 0.00558, -0.021, -0.0141, -0.0401],
          [0.25, 0.00722, -0.00611, 0.0735, -0.00794, -0.195, 0.00323, 0.0165, 7.45e-09, 0.0127, ..., -0.0373, -0.00416, 0.0572, 0.0203,
           -0.0602, 0.0551, 0.00033, -0.0248, -0.00409, 

In [18]:
bce_chexpert_exp.evaluate()

234/234 [==============================] - 4s 17ms/step


/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1

234/234 [==============================] - 13s 58ms/step - loss: 0.4400 - auc: 0.7438 - precision: 0.6265 - recall: 0.0952 - f2_score: 0.1147 - binary_accuracy: 0.8130 - accuracy_enlarged_cardiomediastinum: 0.5385 - accuracy_cardiomegaly: 0.7436 - accuracy_lung_opacity: 0.4615 - accuracy_lung_lesion: 0.9829 - accuracy_edema: 0.8761 - accuracy_consolidation: 0.8632 - accuracy_pneumonia: 0.9573 - accuracy_atelectasis: 0.6667 - accuracy_pneumothorax: 0.9487 - accuracy_pleural_effusion: 0.7821 - accuracy_pleural_other: 0.9573 - accuracy_fracture: 0.9786 - auc_enlarged_cardiomediastinum: 0.5079 - auc_cardiomegaly: 0.8016 - auc_lung_opacity: 0.9190 - auc_lung_lesion: 0.6481 - auc_edema: 0.9295 - auc_consolidation: 0.9178 - auc_pneumonia: 0.8108 - auc_atelectasis: 0.8131 - auc_pneumothorax: 0.7514 - auc_pleural_effusion: 0.9315 - auc_pleural_other: 0.8948 - auc_fracture: 0.0000e+00 - precision_enlarged_cardiomediastinum: 1.0000 - precision_cardiomegaly: 1.0000 - precision_lung_opacity: 0.0000

{'report': '                            precision    recall  f1-score   support\n\nEnlarged Cardiomediastinum       1.00      0.01      0.02       109\n              Cardiomegaly       1.00      0.12      0.21        68\n              Lung Opacity       0.00      0.00      0.00       126\n               Lung Lesion       0.00      0.00      0.00         1\n                     Edema       0.86      0.42      0.57        45\n             Consolidation       1.00      0.03      0.06        33\n                 Pneumonia       0.25      0.12      0.17         8\n               Atelectasis       1.00      0.03      0.05        80\n              Pneumothorax       0.25      0.25      0.25         8\n          Pleural Effusion       0.90      0.27      0.41        67\n             Pleural Other       0.00      0.00      0.00         1\n                  Fracture       0.00      0.00      0.00         0\n\n                 micro avg       0.63      0.10      0.17       546\n                 m

In [19]:
benchmark.as_dict()

{'benchmark_name': 'Ensemble_Sharp21_U75_C0_N12_SGD',
 'dataset_name': 'chexpert_full',
 'dataset_folder': 'data/chexpert/full',
 'models_dir': 'models',
 'epochs': 3,
 'optimizer': 'Adam',
 'learning_rate': 0.001,
 'lr_factor': 1.0,
 'loss': 'binary_crossentropy',
 'use_class_weights': False,
 'class_weights': [1.0471136569976807,
  0.8615774512290955,
  0.21405130624771118,
  1.2290253639221191,
  0.3829084038734436,
  1.5654457807540894,
  0.9355764389038086,
  0.3477109670639038,
  1.1680023670196533,
  0.27839189767837524,
  1.1709423065185547,
  0.7992541790008545],
 'positive_weights': [1.0471136569976807,
  0.8615774512290955,
  0.21405130624771118,
  1.2290253639221191,
  0.3829084038734436,
  1.5654457807540894,
  0.9355764389038086,
  0.3477109670639038,
  1.1680023670196533,
  0.27839189767837524,
  1.1709423065185547,
  0.7992541790008545],
 'negative_weights': [0.7336834073066711,
  0.7509576678276062,
  1.2557218074798584,
  0.7222639918327332,
  0.9005477428436279,
  0.

In [4]:
#get_experiment_from_logs, benchmark_from_logs, get_preprocessing_for_architecture, get_model_build_function

In [24]:
exp_dict = get_experiment_from_logs(name="DenseNet121_Chexpert_CWBCE_L1Normed_E3_B32_C0_N12_AugAffine_sharp21_U75_D256_DS9505_5LR1_LF1_SGD_Upsampled")
experiment = rebuild_experiment(exp_dict, epoch=2)
experiment.evaluate()
difference_test_results(exp_dict["test"], experiment.evaluation_result["metrics"])

Using weights file weights.02-0.21.hdf5 to load model...


In [25]:
experiment.evaluate()

234/234 [==============================] - 4s 16ms/step


/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1

234/234 [==============================] - 13s 55ms/step - loss: 0.2987 - auc: 0.7419 - precision: 0.6453 - recall: 0.1016 - f2_score: 0.1222 - binary_accuracy: 0.8145 - accuracy_enlarged_cardiomediastinum: 0.5385 - accuracy_cardiomegaly: 0.7479 - accuracy_lung_opacity: 0.4615 - accuracy_lung_lesion: 0.9786 - accuracy_edema: 0.8761 - accuracy_consolidation: 0.8632 - accuracy_pneumonia: 0.9530 - accuracy_atelectasis: 0.6709 - accuracy_pneumothorax: 0.9530 - accuracy_pleural_effusion: 0.7991 - accuracy_pleural_other: 0.9744 - accuracy_fracture: 0.9744 - auc_enlarged_cardiomediastinum: 0.5631 - auc_cardiomegaly: 0.8136 - auc_lung_opacity: 0.9188 - auc_lung_lesion: 0.5665 - auc_edema: 0.9261 - auc_consolidation: 0.9123 - auc_pneumonia: 0.8072 - auc_atelectasis: 0.8151 - auc_pneumothorax: 0.7315 - auc_pleural_effusion: 0.9338 - auc_pleural_other: 0.8884 - auc_fracture: 0.0000e+00 - precision_enlarged_cardiomediastinum: 1.0000 - precision_cardiomegaly: 0.8462 - precision_lung_opacity: 0.0000

{'report': '                            precision    recall  f1-score   support\n\nEnlarged Cardiomediastinum       1.00      0.01      0.02       109\n              Cardiomegaly       0.85      0.16      0.27        68\n              Lung Opacity       0.00      0.00      0.00       126\n               Lung Lesion       0.00      0.00      0.00         1\n                     Edema       0.83      0.44      0.58        45\n             Consolidation       1.00      0.03      0.06        33\n                 Pneumonia       0.00      0.00      0.00         8\n               Atelectasis       1.00      0.04      0.07        80\n              Pneumothorax       0.20      0.12      0.15         8\n          Pleural Effusion       0.92      0.33      0.48        67\n             Pleural Other       0.00      0.00      0.00         1\n                  Fracture       0.00      0.00      0.00         0\n\n                 micro avg       0.66      0.11      0.19       546\n                 m

In [26]:
difference_test_results(exp_dict["test"], experiment.evaluation_result["metrics"])

{'loss': 0.00406038761138916,
 'auc': 0.0018503069877624512,
 'precision': 0.01884281635284424,
 'recall': 0.006410256028175354,
 'f2_score': 0.007557682693004608,
 'binary_accuracy': 0.0014247894287109375,
 'accuracy_enlarged_cardiomediastinum': 0.0,
 'accuracy_cardiomegaly': 0.004273474216461182,
 'accuracy_lung_opacity': 0.0,
 'accuracy_lung_lesion': 0.004273533821105957,
 'accuracy_edema': 0.0,
 'accuracy_consolidation': 0.0,
 'accuracy_pneumonia': 0.004273533821105957,
 'accuracy_atelectasis': 0.004273474216461182,
 'accuracy_pneumothorax': 0.004273474216461182,
 'accuracy_pleural_effusion': 0.017094016075134277,
 'accuracy_pleural_other': 0.017094016075134277,
 'accuracy_fracture': 0.004273474216461182,
 'auc_enlarged_cardiomediastinum': 0.055192649364471436,
 'auc_cardiomegaly': 0.011915266513824463,
 'auc_lung_opacity': 0.0001469254493713379,
 'auc_lung_lesion': 0.08154511451721191,
 'auc_edema': 0.0034096837043762207,
 'auc_consolidation': 0.005427420139312744,
 'auc_pneumonia